In [25]:
import os
import tensorflow as tf
import xml.etree.ElementTree as ET
from PIL import Image
import numpy as np
import pickle

In [26]:
#This function takes the path of an individual xml file and prints the filename, stroke number and all x,y coordinates.
def extraction_of_xy_coordinate_from_xml(xml_file_name):
    filename = os.path.basename(xml_file_name).split('.')[0]
    print(filename)
    tree = ET.parse(xml_file_name)
    root = tree.getroot()
    for i in range(len(root[1])):
        print(i)
        stroke = root[1][i]
        for coordinates in stroke:
           print(coordinates.attrib['x'], coordinates.attrib['y'])


#extraction_of_xy_coordinate_from_xml("/home/digitalscholarship/Projects/handwriting/data/lineStrokes/a01/a01-000/a01-000u-01.xml")

In [27]:
#Takes a root directory and returns the filenames of all xml files in subdirectories 
def xml_directory(path):
    for dir_name, sub_dirs, files in os.walk(path):
        for x in files:
            #print(os.path.join(dir_name, x))
            extraction_of_xy_coordinate_from_xml(os.path.join(dir_name, x))
#xml_directories('/home/digitalscholarship/Projects/handwriting/data/lineStrokes/')

In [48]:
#This function takes the path of an individual xml file and prints the filename, stroke number and all x,y coordinates.
def create_dictionary_from_xml(xml_file_name):
    dict = {}
    filename = os.path.basename(xml_file_name).split('.')[0]
    dict['filename'] = filename
    tree = ET.parse(xml_file_name)
    root = tree.getroot()
    strokes_list = []
    for i in range(len(root[1])):
        x_list = []
        y_list = []
        stroke = root[1][i]
        for coordinates in stroke:
            x_list.append(int(coordinates.attrib['x']))
            y_list.append(int(coordinates.attrib['y']))
        
        stroke_list = [x_list, y_list]
        strokes_list.append(stroke_list)
        dict['strokes'] = strokes_list
    #print(dict)
    return dict
           #print(coordinates.attrib['x'], coordinates.attrib['y'])
#[[107,106],[96,113]]
#create a list of x,y lists [ [[x1, x2],[y1,y2]], []... ]

create_dictionary_from_xml("/home/digitalscholarship/Projects/handwriting/data/lineStrokes/a01/a01-000/a01-000u-01.xml")

{'filename': 'a01-000u-01',
 'strokes': [[[1073,
    1072,
    1066,
    1052,
    1030,
    1009,
    994,
    980,
    971,
    968,
    966,
    972,
    978,
    991,
    1003,
    1016,
    1021,
    1030,
    1040,
    1049,
    1055,
    1058,
    1064,
    1071,
    1071,
    1074,
    1083,
    1097,
    1114,
    1134,
    1158,
    1181,
    1200,
    1218,
    1220,
    1223,
    1221,
    1220,
    1215,
    1204],
   [1058,
    1085,
    1117,
    1152,
    1196,
    1242,
    1286,
    1317,
    1336,
    1344,
    1339,
    1340,
    1320,
    1298,
    1266,
    1231,
    1184,
    1143,
    1108,
    1077,
    1049,
    1021,
    1006,
    1006,
    1006,
    1013,
    1042,
    1082,
    1124,
    1172,
    1225,
    1280,
    1327,
    1365,
    1373,
    1376,
    1372,
    1369,
    1353,
    1330]],
  [[1176,
    1175,
    1171,
    1169,
    1158,
    1139,
    1118,
    1092,
    1065,
    1041,
    1024,
    1015,
    1010,
    1014],
   [1237,
    1233,
    1

In [29]:
def parse_dict(dict):
  
  class_name = dict["filename"]
  inkarray = dict["strokes"]
  stroke_lengths = [len(stroke[0]) for stroke in inkarray]
  total_points = sum(stroke_lengths)
  np_ink = np.zeros((total_points, 3), dtype=np.float32)
  current_t = 0
  for stroke in inkarray:
    for i in [0, 1]:
      np_ink[current_t:(current_t + len(stroke[0])), i] = stroke[i]
    current_t += len(stroke[0])
    np_ink[current_t - 1, 2] = 1  # stroke_end
  # Preprocessing.
  # 1. Size normalization.
  lower = np.min(np_ink[:, 0:2], axis=0)
  upper = np.max(np_ink[:, 0:2], axis=0)
  scale = upper - lower
  scale[scale == 0] = 1
  np_ink[:, 0:2] = (np_ink[:, 0:2] - lower) / scale
  # 2. Compute deltas.
  np_ink = np_ink[1:, 0:2] - np_ink[0:-1, 0:2]
  return np_ink, class_name

In [47]:
dict = create_dictionary_from_xml("/home/digitalscholarship/Projects/handwriting/data/lineStrokes/a01/a01-000/a01-000u-01.xml")
parse_dict(dict)

(array([[-0.00018031,  0.04584041],
        [-0.00108186,  0.05432934],
        [-0.00252434,  0.05942279],
        ..., 
        [ 0.0016228 ,  0.02886248],
        [-0.00090158,  0.00339562],
        [ 0.00054097,  0.00679117]], dtype=float32), 'a01-000u-01')

In [35]:

def img_directories(root):
    width_list = []
    height_list = []
    for dir_name, sub_dirs, files in os.walk(root):
        for x in files:
            #print(os.path.join(dir_name, x))
            im = Image.open(os.path.join(dir_name, x))
            
            
            width,height = im.size
            width_list.append(width)
            height_list.append(height)
    print(max(width_list),min(width_list))
    print(max(height_list),min(height_list))
img_directories('/home/digitalscholarship/Projects/handwriting/data/lineImages')            

3460 77
1377 43


In [38]:
#from https://github.com/hardmaru/write-rnn-tensorflow/blob/master/utils.py
class DataLoader():
    def __init__(
            self,
            batch_size=50,
            seq_length=300,
            scale_factor=10,
            limit=500):
        self.data_dir = "./data"
        self.batch_size = batch_size
        self.seq_length = seq_length
        self.scale_factor = scale_factor  # divide data by this factor
        self.limit = limit  # removes large noisy gaps in the data

        data_file = os.path.join(self.data_dir, "strokes_training_data.cpkl")
        raw_data_dir = self.data_dir + "/lineStrokes"

        if not (os.path.exists(data_file)):
            print("creating training data pkl file from raw source")
            self.preprocess(raw_data_dir, data_file)

        self.load_preprocessed(data_file)
        self.reset_batch_pointer()

    def preprocess(self, data_dir, data_file):
        # create data file from raw xml files from iam handwriting source.

        # build the list of xml files
        filelist = []
        # Set the directory you want to start from
        rootDir = data_dir
        for dirName, subdirList, fileList in os.walk(rootDir):
            #print('Found directory: %s' % dirName)
            for fname in fileList:
                #print('\t%s' % fname)
                filelist.append(dirName + "/" + fname)

        # function to read each individual xml file
        def getStrokes(filename):
            tree = ET.parse(filename)
            root = tree.getroot()

            result = []

            x_offset = 1e20
            y_offset = 1e20
            y_height = 0
            for i in range(1, 4):
                x_offset = min(x_offset, float(root[0][i].attrib['x']))
                y_offset = min(y_offset, float(root[0][i].attrib['y']))
                y_height = max(y_height, float(root[0][i].attrib['y']))
            y_height -= y_offset
            x_offset -= 100
            y_offset -= 100

            for stroke in root[1].findall('Stroke'):
                points = []
                for point in stroke.findall('Point'):
                    points.append(
                        [float(point.attrib['x']) - x_offset, float(point.attrib['y']) - y_offset])
                result.append(points)

            return result

        # converts a list of arrays into a 2d numpy int16 array
        def convert_stroke_to_array(stroke):

            n_point = 0
            for i in range(len(stroke)):
                n_point += len(stroke[i])
            stroke_data = np.zeros((n_point, 3), dtype=np.int16)

            prev_x = 0
            prev_y = 0
            counter = 0

            for j in range(len(stroke)):
                for k in range(len(stroke[j])):
                    stroke_data[counter, 0] = int(stroke[j][k][0]) - prev_x
                    stroke_data[counter, 1] = int(stroke[j][k][1]) - prev_y
                    prev_x = int(stroke[j][k][0])
                    prev_y = int(stroke[j][k][1])
                    stroke_data[counter, 2] = 0
                    if (k == (len(stroke[j]) - 1)):  # end of stroke
                        stroke_data[counter, 2] = 1
                    counter += 1
            return stroke_data

        # build stroke database of every xml file inside iam database
        strokes = []
        for i in range(len(filelist)):
            if (filelist[i][-3:] == 'xml'):
                print('processing ' + filelist[i])
                strokes.append(
                    convert_stroke_to_array(
                        getStrokes(
                            filelist[i])))

        f = open(data_file, "wb")
        pickle.dump(strokes, f, protocol=2)
        f.close()

    def load_preprocessed(self, data_file):
        f = open(data_file, "rb")
        self.raw_data = pickle.load(f)
        f.close()

        # goes thru the list, and only keeps the text entries that have more
        # than seq_length points
        self.data = []
        self.valid_data = []
        counter = 0

        # every 1 in 20 (5%) will be used for validation data
        cur_data_counter = 0
        for data in self.raw_data:
            if len(data) > (self.seq_length + 2):
                # removes large gaps from the data
                data = np.minimum(data, self.limit)
                data = np.maximum(data, -self.limit)
                data = np.array(data, dtype=np.float32)
                data[:, 0:2] /= self.scale_factor
                cur_data_counter = cur_data_counter + 1
                if cur_data_counter % 20 == 0:
                    self.valid_data.append(data)
                else:
                    self.data.append(data)
                    # number of equiv batches this datapoint is worth
                    counter += int(len(data) / ((self.seq_length + 2)))

        print("train data: {}, valid data: {}".format(
            len(self.data), len(self.valid_data)))
        # minus 1, since we want the ydata to be a shifted version of x data
        self.num_batches = int(counter / self.batch_size)

    def validation_data(self):
        # returns validation data
        x_batch = []
        y_batch = []
        for i in range(self.batch_size):
            data = self.valid_data[i % len(self.valid_data)]
            idx = 0
            x_batch.append(np.copy(data[idx:idx + self.seq_length]))
            y_batch.append(np.copy(data[idx + 1:idx + self.seq_length + 1]))
        return x_batch, y_batch

    def next_batch(self):
        # returns a randomised, seq_length sized portion of the training data
        x_batch = []
        y_batch = []
        for i in range(self.batch_size):
            data = self.data[self.pointer]
            # number of equiv batches this datapoint is worth
            n_batch = int(len(data) / ((self.seq_length + 2)))
            idx = random.randint(0, len(data) - self.seq_length - 2)
            x_batch.append(np.copy(data[idx:idx + self.seq_length]))
            y_batch.append(np.copy(data[idx + 1:idx + self.seq_length + 1]))
            # adjust sampling probability.
            if random.random() < (1.0 / float(n_batch)):
                # if this is a long datapoint, sample this data more with
                # higher probability
                self.tick_batch_pointer()
        return x_batch, y_batch

    def tick_batch_pointer(self):
        self.pointer += 1
        if (self.pointer >= len(self.data)):
            self.pointer = 0

    def reset_batch_pointer(self):
        self.pointer = 0


In [39]:
data_loader = DataLoader(50, 300, 20)

train data: 11035, valid data: 580


In [9]:
data = pickle.load(open("/home/digitalscholarship/Projects/handwriting/data/strokes_training_data.cpkl", 'rb'))

In [10]:
for line in data:
    print(line)

[[163 464   1]
 [ -1   1   0]
 [  5   7   0]
 ..., 
 [-16  13   0]
 [  2  10   0]
 [ 10   0   1]]
[[100 317   0]
 [ 12  15   0]
 [  4   5   0]
 ..., 
 [ 55  -4   0]
 [ 44   0   0]
 [ 37   2   1]]
[[117 415   0]
 [-14  -1   0]
 [ -2  -3   0]
 ..., 
 [-19 -14   0]
 [-10  -6   0]
 [-11  -6   1]]
[[235 706   0]
 [  3   0   0]
 [ -4  -7   0]
 ..., 
 [-11  19   0]
 [ -5  15   0]
 [  4  11   1]]
[[227 499   0]
 [  4   4   0]
 [ -3  -8   0]
 ..., 
 [ 61  -7   0]
 [ 65  -2   0]
 [ 45   3   1]]
[[270 499   0]
 [  5 -17   0]
 [  4 -23   0]
 ..., 
 [  8  -1   0]
 [ -8   1   0]
 [  9   3   1]]
[[108 505   0]
 [ -5  -9   0]
 [ -1  -8   0]
 ..., 
 [  2  -2   0]
 [  0  -7   0]
 [  5  -8   1]]
[[157 242   0]
 [  0   9   0]
 [  0   4   0]
 ..., 
 [ 12  -1   0]
 [ 11  -5   0]
 [ -1 -15   1]]
[[300 442   0]
 [  2   0   0]
 [  0  -5   0]
 ..., 
 [-10  11   0]
 [-12  21   0]
 [-20   4   1]]
[[252 279   0]
 [ 23  24   0]
 [ -1   0   0]
 ..., 
 [  3   1   0]
 [  4  -2   0]
 [  4 -10   1]]
[[300 617   0]
 [  0

 [  2  -5   1]]
[[144 375   0]
 [  2   9   0]
 [  0   8   0]
 ..., 
 [  1 -26   0]
 [ 13 -25   0]
 [ 23 -21   1]]
[[101 430   0]
 [ -1  -1   0]
 [  0   0   0]
 ..., 
 [ 28   7   0]
 [ 22   1   0]
 [ 27   3   1]]
[[201 292   0]
 [  1  -8   0]
 [  0  -8   0]
 ..., 
 [-17   4   0]
 [-26   2   0]
 [-20   1   1]]
[[100 217   0]
 [  0   3   0]
 [  0   5   0]
 ..., 
 [ 30   2   0]
 [ 35   6   0]
 [ 34   7   1]]
[[100 258   0]
 [  8   5   0]
 [  7  12   0]
 ..., 
 [-19  16   0]
 [ -6   4   0]
 [  2  -6   1]]
[[196 363   0]
 [ -9  -3   0]
 [ -9   0   0]
 ..., 
 [ 29  -2   0]
 [ 29  -2   0]
 [ 18  -9   1]]
[[100 270   0]
 [  0   0   0]
 [  0   0   0]
 ..., 
 [-13  20   0]
 [ -7  19   0]
 [ -5  13   1]]
[[149 263   0]
 [ -7   8   0]
 [ -8   4   0]
 ..., 
 [-34  -2   0]
 [-26  -8   0]
 [-25 -12   1]]
[[100 118   0]
 [ 22  22   0]
 [  0   8   0]
 ..., 
 [ 24  -3   0]
 [ 25  -2   0]
 [ 22  -6   1]]
[[100 312   0]
 [  0   3   0]
 [  2   4   0]
 ..., 
 [ -3  -2   0]
 [ -4  -2   0]
 [-18 -10   1]]
[[10

 [ -9  13   1]]
[[380 373   0]
 [  2 -12   0]
 [ -2 -12   0]
 ..., 
 [  6  -5   0]
 [  5  -5   0]
 [ 26   9   1]]
[[362 425   0]
 [ -2  -4   0]
 [ -4   0   0]
 ..., 
 [-36  -8   0]
 [-26  -5   0]
 [-21  -1   1]]
[[132 316   0]
 [ -4   8   0]
 [ -4   4   0]
 ..., 
 [ -1   0   0]
 [  0   0   0]
 [ -3   3   1]]
[[100 293   0]
 [  2  12   0]
 [  2  16   0]
 ..., 
 [ -2  -4   0]
 [  2  -7   0]
 [  1  -7   1]]
[[102 182   0]
 [ -2  -1   0]
 [  0   0   0]
 ..., 
 [-22 -20   0]
 [-12 -25   0]
 [-14 -24   1]]
[[122 308   0]
 [ -3  -8   0]
 [  0   4   0]
 ..., 
 [ 12  12   0]
 [ 10   6   0]
 [ 23  -1   1]]
[[118 340   0]
 [ -3   0   0]
 [ -1   8   0]
 ..., 
 [ 14  -4   0]
 [  5  -4   0]
 [  9   0   1]]
[[225 150   0]
 [ -9   1   0]
 [-11   0   0]
 ..., 
 [-27  42   0]
 [-27  37   0]
 [-27  25   1]]
[[188 333   0]
 [ -2   0   0]
 [ -3  -7   0]
 ..., 
 [ -8  29   0]
 [ -5  33   0]
 [ -6  29   1]]
[[101 547   0]
 [ -1   0   0]
 [  1   4   0]
 ..., 
 [  0   0   0]
 [ -3  -3   0]
 [ -1  -4   1]]
[[10

 [ -2  -3   1]]
[[113 347   0]
 [  1  -4   0]
 [  5  -4   0]
 ..., 
 [ 23  -7   0]
 [ 18  -8   0]
 [  5 -16   1]]
[[232 302   0]
 [ -4   0   0]
 [  1   0   0]
 ..., 
 [-39 -12   0]
 [-37 -15   0]
 [-23 -16   1]]
[[105 483   0]
 [ -1   1   0]
 [ -1  -1   0]
 ..., 
 [ -5  -1   0]
 [  0   1   0]
 [  4   1   1]]
[[100 564   0]
 [  0   0   0]
 [  0  -4   0]
 ..., 
 [  0  -1   0]
 [  1   0   0]
 [  0   0   1]]
[[103 602   1]
 [ -2   0   0]
 [ -1  -1   0]
 ..., 
 [ -5   3   0]
 [  3  14   0]
 [ -3  18   1]]
[[125 564   0]
 [  6   3   0]
 [  1  -1   0]
 ..., 
 [ 20   3   0]
 [  4   2   0]
 [ -4  -2   1]]
[[112 240   1]
 [  4   7   0]
 [ -4  -3   0]
 ..., 
 [  1  -6   0]
 [  0  -3   0]
 [ -7  -7   1]]
[[130 419   0]
 [ -1   0   0]
 [ -4  -4   0]
 ..., 
 [  3   2   0]
 [  4   2   0]
 [ -1   5   1]]
[[208 464   0]
 [ -2  28   0]
 [ -1  32   0]
 ..., 
 [ 44 -19   0]
 [ 55 -14   0]
 [ 46 -25   1]]
[[245 635   0]
 [-12   3   0]
 [-12  -1   0]
 ..., 
 [  6  17   0]
 [  1  22   0]
 [ -2  19   1]]
[[12

 [  8   2   1]]
[[294 148   0]
 [ 12  12   0]
 [ -2  -1   0]
 ..., 
 [  4  -1   0]
 [  2  -3   0]
 [-12  -7   1]]
[[156 293   0]
 [  3   3   0]
 [  4   1   0]
 ..., 
 [  1  -3   0]
 [  5  -2   0]
 [  3  -7   1]]
[[ 120  324    0]
 [  -2   -4    0]
 [  -2   12    0]
 [  -3   16    0]
 [   2   40    0]
 [  -9   36    0]
 [   4   44    0]
 [ 103  -11    0]
 [  47    9    0]
 [  32   11    0]
 [  26   11    0]
 [  19   12    0]
 [  10   12    0]
 [   6   -4    0]
 [  -9  -16    0]
 [ -19  -36    1]
 [-186 -356    0]
 [ -31    4    0]
 [  -3    7    0]
 [  -5    4    0]
 [   9    5    1]
 [ 608   75    0]
 [  22   30    0]
 [   6   36    0]
 [   2   56    0]
 [  -7   77    0]
 [   3   60    0]
 [  -5   32    0]
 [  -7   16    0]
 [  -5   -3    0]
 [  -3   -4    0]
 [  -7  -16    0]
 [   1   -7    0]
 [   6   -9    0]
 [  23   -2    0]
 [  26   -5    0]
 [  16   -6    0]
 [  18  -13    0]
 [  19  -18    0]
 [  14  -18    0]
 [   6  -24    0]
 [   6  -37    0]
 [   7  -41    0]
 [  10  -38   

...

[[171 557   0]
 [ -7  -4   0]
 [ -5  -5   0]
 ..., 
 [ 35   9   0]
 [  1  -2   0]
 [ -3  -2   1]]
[[101 614   0]
 [ -1  12   0]
 [  2  -4   0]
 ..., 
 [  7   4   0]
 [  3   5   0]
 [  3   4   1]]
[[305 486   0]
 [ -1  -9   0]
 [ -5 -13   0]
 ..., 
 [  0   1   0]
 [ -1   4   0]
 [ -4   3   1]]
[[105 433   0]
 [ -3   0   0]
 [ -2   0   0]
 ..., 
 [  0   0   0]
 [  4   1   0]
 [  4   2   1]]
[[167 638   0]
 [  5   5   0]
 [ -1 -12   0]
 ..., 
 [ -4   0   0]
 [  0  -2   0]
 [  0  -1   1]]
[[102 540   0]
 [  3   8   0]
 [ -2   0   0]
 ..., 
 [ -1   1   0]
 [  1  -1   0]
 [  0   0   1]]
[[120 140   1]
 [  5  27   0]
 [  1  32   0]
 ..., 
 [  0   0   0]
 [ -2   5   0]
 [ -3  -2   1]]
[[226 359   0]
 [  7 -21   0]
 [  4 -25   0]
 ..., 
 [ 19  15   0]
 [ 29   4   0]
 [ 37  -3   1]]
[[106 339   0]
 [ -2   0   0]
 [  0   1   0]
 ..., 
 [ -1   1   0]
 [  1   7   0]
 [ -5   0   1]]
[[300 252   0]
 [  0  -4   0]
 [ -2  -4   0]
 ..., 
 [  7   3   0]
 [ -3  -3   0]
 [  2  -5   1]]
[[141 180   0]
 [ -1

[[232 516   0]
 [  4   4   0]
 [  4  -5   0]
 ..., 
 [ 50   3   0]
 [ 62   2   0]
 [ 54   7   1]]
[[114 492   0]
 [  0   0   0]
 [  0   0   0]
 ..., 
 [ -1   1   0]
 [ -5   3   0]
 [ -2   6   1]]
[[220 209   0]
 [  8  16   0]
 [  0   4   0]
 ..., 
 [  0   1   0]
 [-11  11   0]
 [-10   8   1]]
[[262 269   0]
 [ -1  -9   0]
 [  0   0   0]
 ..., 
 [  3   2   0]
 [  1  -1   0]
 [  3  -4   1]]
[[211 122   0]
 [ 22  25   0]
 [ -2  -3   0]
 ..., 
 [ 50 -13   0]
 [ 46 -17   0]
 [ 58 -14   1]]
[[177 240   0]
 [ -7 -11   0]
 [ -7  -5   0]
 ..., 
 [-25  -5   0]
 [-23 -17   0]
 [-21 -31   1]]
[[123 241   0]
 [  2   4   0]
 [  1  -1   0]
 ..., 
 [-12  32   0]
 [ -8  21   0]
 [  2  15   1]]
[[102 286   0]
 [  1  -3   0]
 [ -2   0   0]
 ..., 
 [ -3  -2   0]
 [  0   0   0]
 [  2   4   1]]
[[128 247   0]
 [  0  -3   0]
 [  1   0   0]
 ..., 
 [ 20 -16   0]
 [ 30 -16   0]
 [ 36 -11   1]]
[[134 178   0]
 [ -2   4   0]
 [  0   5   0]
 ..., 
 [-17   5   0]
 [-13 -12   0]
 [-17 -23   1]]
[[113 246   0]
 [ -2

 [ 26  14   1]]
[[276 417   0]
 [  0  -3   0]
 [  7 -12   0]
 ..., 
 [  8   2   0]
 [ -2  -3   0]
 [  5  -1   1]]
[[143 229   0]
 [ -2   8   0]
 [  2   5   0]
 ..., 
 [ 20   5   0]
 [ 19   6   0]
 [ 13   3   1]]
[[148 538   0]
 [ -8   3   0]
 [  0   0   0]
 ..., 
 [ 39   3   0]
 [ 39   7   0]
 [ 24   7   1]]
[[100 390   0]
 [  2   0   0]
 [  1   1   0]
 ..., 
 [ 33  11   0]
 [ 27   6   0]
 [ 14   1   1]]
[[184 380   0]
 [ -7 -10   0]
 [ -6  -5   0]
 ..., 
 [ 15  25   0]
 [ 17  20   0]
 [ 16  12   1]]
[[153 215   0]
 [ -1   3   0]
 [  2   1   0]
 ..., 
 [ 37  12   0]
 [ 27   5   0]
 [ 19  -3   1]]
[[148 280   0]
 [ 13  20   0]
 [ -3   0   0]
 ..., 
 [ 38 -10   0]
 [ 31  -9   0]
 [ 17  -8   1]]
[[ 204  169    0]
 [ -12    8    0]
 [  -8    8    0]
 [ -16   11    0]
 [ -14   23    0]
 [ -20   26    0]
 [ -14   31    0]
 [ -12   36    0]
 [  -8   35    0]
 [   1   32    0]
 [   8   33    0]
 [  11   21    0]
 [  17   12    0]
 [  20    7    0]
 [  27   -3    0]
 [  27  -18    0]
 [  27  -2

[[248 416   0]
 [  0   0   0]
 [ -3  -4   0]
 ..., 
 [ -7  10   0]
 [-12   9   0]
 [-10  -7   1]]
[[227 101   0]
 [-16  -1   0]
 [-13  11   0]
 ..., 
 [ 27  17   0]
 [ 38   5   0]
 [ 28 -10   1]]
[[136 455   1]
 [ 30   1   0]
 [ 22 -11   0]
 ..., 
 [  5   1   0]
 [  1  -1   0]
 [ -5   5   1]]
[[144 384   0]
 [ 12 -20   0]
 [  8 -24   0]
 ..., 
 [  6   6   0]
 [  5   1   0]
 [  0  -8   1]]
[[158 196   0]
 [ -4   9   0]
 [ -3  24   0]
 ..., 
 [-21  12   0]
 [-32  15   0]
 [-40  13   1]]
[[242 490   0]
 [ -3   0   0]
 [ -4  -8   0]
 ..., 
 [  5  19   0]
 [  0   7   0]
 [ -7  -5   1]]
[[232 490   0]
 [-16  -1   0]
 [-15  -5   0]
 ..., 
 [  0  14   0]
 [  1  11   0]
 [ -2  11   1]]
[[135 430   0]
 [  4  23   0]
 [  9  32   0]
 ..., 
 [  0   0   0]
 [  6   5   0]
 [  5  -1   1]]
[[182 375   0]
 [ -3   3   0]
 [  1   0   0]
 ..., 
 [  4   1   0]
 [ -4  -1   0]
 [ -4   0   1]]
[[247 478   0]
 [ -2  -8   0]
 [ -4 -12   0]
 ..., 
 [ -1   6   0]
 [ -2   7   0]
 [ -1   6   1]]
[[148 380   0]
 [ -1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [46]:
import pprint 
from matplotlib.pyplot import imshow

def getStrokes(filename):
            label = os.path.basename(filename).split('.')[0]
            im = Image.open(filename.split('.')[0].replace('lineStrokes','lineImages') + '.tif')
            #im.show()
            tree = ET.parse(filename)
            root = tree.getroot()

            result = []

            x_offset = 1e20
            y_offset = 1e20
            y_height = 0
            for i in range(1, 4):
                x_offset = min(x_offset, float(root[0][i].attrib['x']))
                y_offset = min(y_offset, float(root[0][i].attrib['y']))
                y_height = max(y_height, float(root[0][i].attrib['y']))
            y_height -= y_offset
            x_offset -= 100
            y_offset -= 100

            for stroke in root[1].findall('Stroke'):
                points = []
                for point in stroke.findall('Point'):
                    points.append(
                        [float(point.attrib['x']) - x_offset, float(point.attrib['y']) - y_offset])
                result.append(points)
            dict = {}
            dict['label'] = label
            dict['points'] = result
            return dict 
        
data = getStrokes("/home/digitalscholarship/Projects/handwriting/data/lineStrokes/a01/a01-000/a01-000u-01.xml")
pp = pprint.PrettyPrinter(indent=4)
pp.pprint(data)

{   'label': 'a01-000u-01',
    'points': [   [   [207.0, 371.0],
                      [206.0, 398.0],
                      [200.0, 430.0],
                      [186.0, 465.0],
                      [164.0, 509.0],
                      [143.0, 555.0],
                      [128.0, 599.0],
                      [114.0, 630.0],
                      [105.0, 649.0],
                      [102.0, 657.0],
                      [100.0, 652.0],
                      [106.0, 653.0],
                      [112.0, 633.0],
                      [125.0, 611.0],
                      [137.0, 579.0],
                      [150.0, 544.0],
                      [155.0, 497.0],
                      [164.0, 456.0],
                      [174.0, 421.0],
                      [183.0, 390.0],
                      [189.0, 362.0],
                      [192.0, 334.0],
                      [198.0, 319.0],
                      [205.0, 319.0],
                      [205.0, 319.0],
                      